# Session 5: Linguistics

## Getting started

First, we will load the packages we need for these exercises.

In [1]:
# From base python
from collections import Counter            # Counters
import csv                                 # Read and write csv files
import os                                  # Work with file paths
import re                                  # Regular expressions 

# External
from bs4 import BeautifulSoup              # HTML (and XML) parsing
import nltk                                # Natural Language Toolkit -- for NLP parsing
import numpy as np                         # Simple mathematics function and linear algebra
import spacy                               # SpaCy -- for NLP parsing
import requests                            # A better interface for http connections

To start, we need to load in the text data from last session and process it again.

In [2]:
with open('../../Data/S4_WSJ_2013.09.09.txt', 'rt') as f:
    text2 = f.readlines()

A lot of work with text analytics typically goes into cleaning up the document.  In the case of the above, we probably want 119 articles separated out such that each article is an element of a list.  To do this, we can use some basic looping and conditional statements.  Note 2 key insights for this:

1. Each article starts with the phrase `Full text: `.  This is unlikely to be used in the article text itself, so it can serve as a delimiter for the start of an article.
2. Articles end with one of the following tags: `Company / organization: `, `Credit: `, or `Copyright: `
3. One article is missing, just saying `Full text: Not available`

In [3]:
articles = []
article = ''
reading = False
for line in text2:
    if reading:  # check for the end of an article
        if 'Company / organization: ' in line or 'Credit: ' in line or 'Copyright: ' in line:
            # Done reading the article: output it
            reading = False
            articles.append(article)
            article = ''
        else:
            article += line
    else:  # check for the start of an article
        if 'Full text: ' in line and 'Full text: Not available' not in line:
            # Start reading the article in
            article = line[11:]
            reading = True
        else:
            pass  # not part of an article, nothing to do.
        

Given the above list, we are now in good shape to do whichever analysis it is that we need.

# Parsing with NLTK

For NLTK, we will take a look at simple part of speech tagging.  To do this, there are two steps:

1. Tokenize the documents
2. Apply PoS tags

In [4]:
# If you get an error that you are missing 'punkt', run: nltk.download('punkt')
article_tokens = [nltk.tokenize.word_tokenize(article) for article in articles]

In [5]:
print(article_tokens[0])

['Hedge', 'funds', 'are', 'cutting', 'their', 'standard', 'fees', 'of', '2', '%', 'of', 'assets', 'under', 'management', 'and', '20', '%', 'of', 'profits', 'amid', 'pressure', 'from', 'investors', '.', '--', '-', 'A', 'team', 'of', 'Ares', 'and', 'CPP', 'Investment', 'Board', 'are', 'in', 'the', 'final', 'stages', 'of', 'talks', 'to', 'buy', 'luxury', 'retailer', 'Neiman', 'Marcus', 'for', 'around', '$', '6', 'billion', '.', '--', '-', 'Federal', 'regulators', 'plan', 'to', 'reduce', 'the', 'maximum', 'size', 'of', 'mortgages', 'eligible', 'for', 'backing', 'by', 'Fannie', 'and', 'Freddie', '.', '--', '-', 'Time', 'Warner', 'plans', 'to', 'move', 'its', 'U.S.', 'retirees', 'from', 'company-administered', 'health', 'plans', 'to', 'private', 'exchanges', '.', '--', '-', 'A', 'U.S.', 'appeals', 'court', 'will', 'hear', 'oral', 'arguments', 'today', 'in', 'a', 'suit', 'by', 'Verizon', 'challenging', 'FCC', '``', 'net-neutrality', "''", 'rules', '.', '--', '-', 'Japan', "'s", 'GDP', 'grew',

Next, we need to import in a Part of Speech (PoS) tagger.  One such tagger is based on the Brown corpus, which is based on news articles that were manually labeled with parts of speech.  NLTK makes this data available for us for free, and we can import it from `nltk.corpus` once we have separately downloaded it.

Then, constructing a tagger is as simple as importing a tagger and passing the tagged corpus to it.

In [6]:
# Requires: nltk.download('brown')
brown_news_tagged = nltk.corpus.brown.tagged_sents(categories='news', tagset='brown')
pos_tagger = nltk.UnigramTagger(brown_news_tagged)

Next, we can apply the built tagger using the `.tag()` method.  As we can see, the below does a reasonable job, but misses certain words that were not in the training data, such as `"Hedge"`.

In [7]:
tagged1 = pos_tagger.tag(article_tokens[0])
print(tagged1)

[('Hedge', None), ('funds', 'NNS'), ('are', 'BER'), ('cutting', 'VBG'), ('their', 'PP$'), ('standard', 'JJ'), ('fees', 'NNS'), ('of', 'IN'), ('2', 'CD'), ('%', None), ('of', 'IN'), ('assets', 'NNS'), ('under', 'IN'), ('management', 'NN'), ('and', 'CC'), ('20', 'CD'), ('%', None), ('of', 'IN'), ('profits', 'NNS'), ('amid', 'IN'), ('pressure', 'NN'), ('from', 'IN'), ('investors', 'NNS'), ('.', '.'), ('--', '--'), ('-', None), ('A', 'AT'), ('team', 'NN'), ('of', 'IN'), ('Ares', None), ('and', 'CC'), ('CPP', None), ('Investment', 'NN-TL'), ('Board', 'NN-TL'), ('are', 'BER'), ('in', 'IN'), ('the', 'AT'), ('final', 'JJ'), ('stages', 'NNS'), ('of', 'IN'), ('talks', 'NNS'), ('to', 'TO'), ('buy', 'VB'), ('luxury', 'NN'), ('retailer', None), ('Neiman', None), ('Marcus', 'NP'), ('for', 'IN'), ('around', 'RB'), ('$', None), ('6', 'CD'), ('billion', 'CD'), ('.', '.'), ('--', '--'), ('-', None), ('Federal', 'JJ-TL'), ('regulators', None), ('plan', 'NN'), ('to', 'TO'), ('reduce', 'VB'), ('the', 'AT')

Another possible tagger is the perceptron tagger from `nltk.pos_tag()`.  This is a simple neural network approach to PoS tagging.  Note that it is able to give a label to the word `"Hedge"`.

In [8]:
#Requires: nltk.download('averaged_perceptron_tagger')
tagged2 = nltk.pos_tag(article_tokens[0])
print(tagged2)

[('Hedge', 'NNP'), ('funds', 'NNS'), ('are', 'VBP'), ('cutting', 'VBG'), ('their', 'PRP$'), ('standard', 'JJ'), ('fees', 'NNS'), ('of', 'IN'), ('2', 'CD'), ('%', 'NN'), ('of', 'IN'), ('assets', 'NNS'), ('under', 'IN'), ('management', 'NN'), ('and', 'CC'), ('20', 'CD'), ('%', 'NN'), ('of', 'IN'), ('profits', 'NNS'), ('amid', 'IN'), ('pressure', 'NN'), ('from', 'IN'), ('investors', 'NNS'), ('.', '.'), ('--', ':'), ('-', ':'), ('A', 'DT'), ('team', 'NN'), ('of', 'IN'), ('Ares', 'NNS'), ('and', 'CC'), ('CPP', 'NNP'), ('Investment', 'NNP'), ('Board', 'NNP'), ('are', 'VBP'), ('in', 'IN'), ('the', 'DT'), ('final', 'JJ'), ('stages', 'NNS'), ('of', 'IN'), ('talks', 'NNS'), ('to', 'TO'), ('buy', 'VB'), ('luxury', 'NN'), ('retailer', 'NN'), ('Neiman', 'NNP'), ('Marcus', 'NNP'), ('for', 'IN'), ('around', 'IN'), ('$', '$'), ('6', 'CD'), ('billion', 'CD'), ('.', '.'), ('--', ':'), ('-', ':'), ('Federal', 'JJ'), ('regulators', 'NNS'), ('plan', 'VBP'), ('to', 'TO'), ('reduce', 'VB'), ('the', 'DT'), ('

In [9]:
nltk.FreqDist(tagged1).most_common()

[(('of', 'IN'), 11),
 (('.', '.'), 11),
 (('--', '--'), 10),
 (('-', None), 10),
 (('the', 'AT'), 9),
 (('a', 'AT'), 9),
 (('in', 'IN'), 6),
 (('%', None), 4),
 (('to', 'TO'), 4),
 (('by', 'IN'), 4),
 (('are', 'BER'), 3),
 (('and', 'CC'), 3),
 (('from', 'IN'), 3),
 (('for', 'IN'), 3),
 (("'s", None), 3),
 ((',', ','), 3),
 (('investors', 'NNS'), 2),
 (('A', 'AT'), 2),
 (('plans', 'NNS'), 2),
 (('its', 'PP$'), 2),
 (('U.S.', 'NP'), 2),
 (('``', '``'), 2),
 (("''", "''"), 2),
 (('at', 'IN'), 2),
 (('on', 'IN'), 2),
 (('Hedge', None), 1),
 (('funds', 'NNS'), 1),
 (('cutting', 'VBG'), 1),
 (('their', 'PP$'), 1),
 (('standard', 'JJ'), 1),
 (('fees', 'NNS'), 1),
 (('2', 'CD'), 1),
 (('assets', 'NNS'), 1),
 (('under', 'IN'), 1),
 (('management', 'NN'), 1),
 (('20', 'CD'), 1),
 (('profits', 'NNS'), 1),
 (('amid', 'IN'), 1),
 (('pressure', 'NN'), 1),
 (('team', 'NN'), 1),
 (('Ares', None), 1),
 (('CPP', None), 1),
 (('Investment', 'NN-TL'), 1),
 (('Board', 'NN-TL'), 1),
 (('final', 'JJ'), 1),
 

In [10]:
nltk.FreqDist(tagged2).most_common()

[(('of', 'IN'), 11),
 (('.', '.'), 11),
 (('--', ':'), 10),
 (('-', ':'), 10),
 (('the', 'DT'), 9),
 (('a', 'DT'), 9),
 (('in', 'IN'), 6),
 (('%', 'NN'), 4),
 (('to', 'TO'), 4),
 (('by', 'IN'), 4),
 (('are', 'VBP'), 3),
 (('and', 'CC'), 3),
 (('from', 'IN'), 3),
 (('for', 'IN'), 3),
 (("'s", 'POS'), 3),
 ((',', ','), 3),
 (('investors', 'NNS'), 2),
 (('A', 'DT'), 2),
 (('its', 'PRP$'), 2),
 (('U.S.', 'NNP'), 2),
 (('``', '``'), 2),
 (("''", "''"), 2),
 (('at', 'IN'), 2),
 (('on', 'IN'), 2),
 (('Hedge', 'NNP'), 1),
 (('funds', 'NNS'), 1),
 (('cutting', 'VBG'), 1),
 (('their', 'PRP$'), 1),
 (('standard', 'JJ'), 1),
 (('fees', 'NNS'), 1),
 (('2', 'CD'), 1),
 (('assets', 'NNS'), 1),
 (('under', 'IN'), 1),
 (('management', 'NN'), 1),
 (('20', 'CD'), 1),
 (('profits', 'NNS'), 1),
 (('amid', 'IN'), 1),
 (('pressure', 'NN'), 1),
 (('team', 'NN'), 1),
 (('Ares', 'NNS'), 1),
 (('CPP', 'NNP'), 1),
 (('Investment', 'NNP'), 1),
 (('Board', 'NNP'), 1),
 (('final', 'JJ'), 1),
 (('stages', 'NNS'), 1),

We can also work directly with bigrams in NLTK.  The `nltk.bigrams` function is helpful for this, as it will automatically chain everything together even after PoS tagging.  We can then filter on any conditions we may be interested in.

The below example uses bigrams to show what the most common words are that preceed a noun of any sort.

In [11]:
# What preceeds a noun?
# Requires: nltk.download('brown') and nltk.download('universal_tagset')
brown_news_tagged = nltk.corpus.brown.tagged_sents(categories='news', tagset='universal')
pos_tagger = nltk.UnigramTagger(brown_news_tagged)
tagged3 = pos_tagger.tag(article_tokens[2])

bigrams = nltk.bigrams(tagged3)
noun_preceders = [a for (a, b) in bigrams if b[1] == 'NOUN']
fdist = nltk.FreqDist(noun_preceders)
fdist.most_common()

[(('the', 'DET'), 99),
 (('a', 'DET'), 27),
 ((',', '.'), 21),
 (('.', '.'), 18),
 (('of', 'ADP'), 18),
 (('The', 'DET'), 13),
 (('to', 'PRT'), 12),
 (('in', 'ADP'), 11),
 (('and', 'CONJ'), 10),
 (("'s", None), 10),
 (('financial', 'ADJ'), 8),
 (('U.S.', 'NOUN'), 8),
 (('that', 'ADP'), 8),
 (("''", '.'), 7),
 (('Wall', 'NOUN'), 6),
 (('some', 'DET'), 5),
 (('policy', 'NOUN'), 5),
 (('says', 'VERB'), 5),
 (('economic', 'ADJ'), 4),
 (('Federal', 'ADJ'), 4),
 (('Fed', None), 4),
 (('was', 'VERB'), 4),
 (('Lehman', 'NOUN'), 4),
 (('raise', 'VERB'), 4),
 (('its', 'DET'), 4),
 (('monetary', 'ADJ'), 4),
 (('their', 'DET'), 3),
 (('taxpayer', 'NOUN'), 3),
 (('with', 'ADP'), 3),
 (('many', 'ADJ'), 3),
 (('an', 'DET'), 3),
 (('his', 'DET'), 3),
 (('investment', 'NOUN'), 3),
 (('would', 'VERB'), 3),
 (('on', 'ADP'), 3),
 (('auto', 'NOUN'), 3),
 (('this', 'DET'), 3),
 (('Five', 'NUM'), 2),
 (('four', 'NUM'), 2),
 (('million', 'NUM'), 2),
 (('for', 'ADP'), 2),
 (('enough', 'ADJ'), 2),
 (('economist

We can also examnine the ways in which words are used in these articles.  Below we will use a hand-coded part of speech file based on WSJ articles themselves, the Penn Treebank.  We will then train a simple tagger using this data, and apply it across all documents.

In [12]:
# How are certain words used?
# Requires: nltk.download('treebank') and nltk.download('universal_tagset')
wsj_tagged = nltk.corpus.treebank.tagged_sents(tagset='universal')
pos_tagger = nltk.UnigramTagger(wsj_tagged)
tagged4 = list(map(pos_tagger.tag, article_tokens))
cfd_w2p = nltk.ConditionalFreqDist([item for sublist in tagged4 for item in sublist])
cfd_p2w = nltk.ConditionalFreqDist([(item[1], item[0]) for sublist in tagged4 for item in sublist])

In [13]:
cfd_w2p['financial']

FreqDist({'ADJ': 52})

In [14]:
cfd_w2p['Wall']

FreqDist({'NOUN': 26})

In [15]:
cfd_w2p['interest']

FreqDist({'NOUN': 31})

We can also explore the frequency of usage of different words within parts of speech.  The `cfd_p2w` object we created earlier will facilitate this.

In [16]:
cfd_p2w['NOUN'].most_common()

[('Mr.', 477),
 ('%', 352),
 ('years', 148),
 ('year', 137),
 ('U.S.', 125),
 ('people', 116),
 ('time', 115),
 ('New', 111),
 ('company', 94),
 ('Ms.', 92),
 ('government', 88),
 ('York', 82),
 ('city', 67),
 ('Sunday', 66),
 ('work', 63),
 ('China', 61),
 ('market', 60),
 ('City', 56),
 ('president', 55),
 ('home', 54),
 ('economy', 53),
 ('Inc.', 53),
 ('part', 52),
 ('companies', 52),
 ('investors', 51),
 ('benefit', 51),
 ('funds', 49),
 ('support', 49),
 ('end', 48),
 ('money', 48),
 ('business', 48),
 ('retirement', 48),
 ('life', 46),
 ('firm', 45),
 ('week', 45),
 ('growth', 44),
 ('day', 44),
 ('month', 43),
 ('Congress', 41),
 ('tax', 41),
 ('country', 40),
 ('Williams', 40),
 ('fees', 39),
 ('House', 39),
 ('markets', 39),
 ('Street', 39),
 ('way', 39),
 ('group', 39),
 ('vote', 38),
 ('days', 38),
 ('White', 37),
 ('months', 37),
 ('system', 36),
 ('prices', 36),
 ('debt', 36),
 ('crisis', 35),
 ('policy', 35),
 ('case', 35),
 ('age', 35),
 ('world', 34),
 ('campaign', 34)

In [17]:
cfd_p2w['VERB'].most_common()

[('is', 665),
 ('said', 421),
 ('are', 409),
 ('was', 387),
 ('have', 355),
 ('has', 345),
 ('be', 314),
 ('will', 236),
 ('had', 195),
 ('would', 192),
 ('were', 148),
 ('can', 144),
 ('been', 132),
 ('do', 126),
 ('could', 118),
 ('says', 100),
 ('did', 83),
 ('make', 69),
 ('according', 65),
 ('take', 61),
 ('including', 58),
 ('go', 54),
 ('made', 54),
 ('get', 53),
 ('may', 52),
 ('say', 50),
 ('want', 48),
 ('going', 45),
 ('being', 44),
 ('need', 43),
 ('help', 40),
 ('left', 38),
 ('use', 38),
 ('become', 37),
 ('play', 37),
 ('put', 36),
 ('pay', 36),
 ('does', 35),
 ('plans', 33),
 ('expected', 33),
 ('know', 32),
 ('see', 32),
 ('should', 31),
 ('working', 31),
 ('give', 30),
 ('set', 30),
 ('win', 29),
 ('began', 29),
 ('used', 28),
 ('come', 28),
 ('might', 28),
 ('keep', 27),
 ('buy', 26),
 ('got', 26),
 ('called', 26),
 ('came', 26),
 ('run', 26),
 ("'re", 26),
 ('spent', 25),
 ('won', 25),
 ('think', 25),
 ("'d", 25),
 ('went', 24),
 ('look', 24),
 ('showed', 24),
 ('fo

In [18]:
cfd_p2w['ADJ'].most_common()

[('more', 273),
 ('other', 110),
 ('new', 99),
 ('most', 97),
 ('many', 83),
 ('such', 81),
 ('first', 75),
 ('last', 66),
 ('past', 54),
 ('financial', 52),
 ('likely', 50),
 ('next', 48),
 ('former', 46),
 ('own', 46),
 ('recent', 44),
 ('few', 42),
 ('same', 41),
 ('public', 40),
 ('big', 38),
 ('early', 38),
 ('economic', 37),
 ('long', 37),
 ('better', 36),
 ('future', 36),
 ('little', 36),
 ('good', 36),
 ('least', 35),
 ('political', 35),
 ('less', 35),
 ('high', 35),
 ('different', 32),
 ('later', 32),
 ('average', 32),
 ('second', 30),
 ('real', 30),
 ('late', 28),
 ('large', 28),
 ('higher', 27),
 ('final', 26),
 ('old', 26),
 ('military', 26),
 ('Democratic', 26),
 ('several', 25),
 ('major', 24),
 ('best', 24),
 ('strong', 24),
 ('latest', 23),
 ('short', 23),
 ('lower', 23),
 ('largest', 23),
 ('private', 22),
 ('local', 22),
 ('Chinese', 22),
 ('current', 21),
 ('mobile', 21),
 ('earlier', 20),
 ('foreign', 20),
 ('sure', 20),
 ('global', 20),
 ('full', 20),
 ('biggest', 

The one issue with a simple unigram tagger is that it ignores context -- it simply applies the most common outcome for a word given the training data.  A bigram tagger can help improve this, but will only match exact bigrams, and thus will not match most of our text.  As such, we can chain these two taggers into 1 tagger, allowing us to match on bigrams first and then fill in the gaps with unigrams.

A neat feature of this is that a word can take on multiple parts of speech, depending on context, as demonstrated below.

In [19]:
# How are certain words used?
# Using a bigram + unigram tagger
# Requires: nltk.download('treebank') and nltk.download('universal_tagset')
wsj_tagged = nltk.corpus.treebank.tagged_sents()
ug = nltk.UnigramTagger(wsj_tagged)
pos_tagger = nltk.BigramTagger(wsj_tagged, backoff=ug)
tagged4 = list(map(pos_tagger.tag, article_tokens))
cfd_w2p = nltk.ConditionalFreqDist([item for sublist in tagged4 for item in sublist])

In [20]:
cfd_w2p['New']

FreqDist({'NNP': 110, 'JJ': 1})

In [21]:
cfd_w2p['Financial']

FreqDist({'NNP': 17, 'JJ': 1})

# Parsing documents using SpaCy

Spacy is a bit more flexible than NLTK, as it provides rather large fully-pretrained models as opposed to providing training corpuses.  The models themselves usually work quite well, but it is important to maintain a set version of the models for a project, as SpaCy does update them somewhat frequently, sometimes introducing breaking changes.

The below code will load in the default English model and process all of our articles.  On a fairly fast computer, this takes around 35 seconds, which is much slower than NLTK.

In [22]:
# install the spacy language model with `python -m spacy download en_core_web_sm`
nlp = spacy.load('en_core_web_sm')

documents = list(nlp.pipe(articles))

At first blush, it doesn't look like SpaCy has done anything with our document!  Outputting the first document reads the same as before processing.

In [23]:
documents[0]

Hedge funds are cutting their standard fees of 2% of assets under management and 20% of profits amid pressure from investors.
---
A team of Ares and CPP Investment Board are in the final stages of talks to buy luxury retailer Neiman Marcus for around $6 billion.
---
Federal regulators plan to reduce the maximum size of mortgages eligible for backing by Fannie and Freddie.
---
Time Warner plans to move its U.S. retirees from company-administered health plans to private exchanges.
---
A U.S. appeals court will hear oral arguments today in a suit by Verizon challenging FCC "net-neutrality" rules.
---
Japan's GDP grew at an annualized pace of 3.8% in the second quarter, much faster than initially estimated.
---
China said its exports rose 7.2% in August from a year earlier, the latest in a series of positive economic reports.
---
White House officials are considering Treasury Undersecretary Lael Brainard for a seat on the Fed's board.
---
SolarCity scrapped a "Happy Meals" deal, a share-le

However, SpaCy actually did quite a bit under the hood.  For instance, it has completed a sentence segmentation task.  We can extract sentences using the generator provided by `.sents`.  Below extracts one potentially interesting sentence.

In [24]:
sent=list(documents[0].sents)[6]
sent

A U.S. appeals court will hear oral arguments today in a suit by Verizon challenging FCC "net-neutrality" rules.

Spacy has also assigned parts of speech to every word, computed a dependency tree (which allows you to see which words are related to which other words), *and* it has computed all entities in the sentence for us.

In [25]:
spacy.displacy.render(sent, style="dep", jupyter=True, options={'compact':True})

In [26]:
spacy.displacy.render(sent, style="ent", jupyter=True)

We can extract entities using the `.ents` property.`

In [27]:
sent.ents

[U.S., today, Verizon, FCC]

As usual with SpaCy, the above isn't actually text -- those elements are all neatly tagged!

In [28]:
for ent in sent.ents:
    print('"' + ent.text + '" is tagged as "' + ent.label_ + '" which comprises of ' + spacy.explain(ent.label_))

"U.S." is tagged as "GPE" which comprises of Countries, cities, states
"today" is tagged as "DATE" which comprises of Absolute or relative dates or periods
"Verizon" is tagged as "ORG" which comprises of Companies, agencies, institutions, etc.
"FCC" is tagged as "ORG" which comprises of Companies, agencies, institutions, etc.


As a couple bonuses, it also calculates out noun chunks and lemmatization.

In [29]:
# Noun chunks
list(sent.noun_chunks)

[A U.S. appeals court,
 oral arguments,
 a suit,
 Verizon challenging FCC "net-neutrality" rules]

In [30]:
# Lemmatization -- like stemming but with an emphasis on grammar (it's more precise)
sent.lemma_

'a U.S. appeal court will hear oral argument today in a suit by Verizon challenge FCC "net-neutrality" rule.'

## Scaling up entity counting

Finding entities in just 1 sentence is a neat trick, but not so useful.  However, SpaCy calculated entities for all sentences back in the `nlp.pipe()` command, so we can scale this up using minimal computing power.

In [31]:
ents = []
for doc in documents:
    ents.append([(ent.text, ent.label_) for ent in doc.ents])
ents = [item for sublist in ents for item in sublist]

In [32]:
Counter(ents).most_common()

[(('U.S.', 'GPE'), 120),
 (('one', 'CARDINAL'), 92),
 (('two', 'CARDINAL'), 82),
 (('first', 'ORDINAL'), 63),
 (('China', 'GPE'), 60),
 (('Sunday', 'DATE'), 59),
 (('Syria', 'GPE'), 49),
 (('Obama', 'PERSON'), 46),
 (('Congress', 'ORG'), 40),
 (('three', 'CARDINAL'), 39),
 (('de Blasio', 'PERSON'), 37),
 (('New York', 'GPE'), 36),
 (('One', 'CARDINAL'), 32),
 (('Williams', 'PERSON'), 31),
 (('Fed', 'ORG'), 29),
 (('today', 'DATE'), 28),
 (('Japan', 'GPE'), 27),
 (('this year', 'DATE'), 27),
 (('2008', 'DATE'), 26),
 (('second', 'ORDINAL'), 26),
 (('Lhota', 'PERSON'), 26),
 (('Abbott', 'PERSON'), 26),
 (('Democratic', 'NORP'), 25),
 (('2010', 'DATE'), 24),
 (('four', 'CARDINAL'), 24),
 (('Saturday', 'DATE'), 23),
 (('Monday', 'DATE'), 22),
 (('Democrats', 'NORP'), 22),
 (('five', 'CARDINAL'), 22),
 (('Mexico', 'GPE'), 21),
 (('Brazil', 'GPE'), 21),
 (('Friday', 'DATE'), 21),
 (('Instagram', 'ORG'), 21),
 (('Europe', 'LOC'), 20),
 (('Chinese', 'NORP'), 20),
 (('Catsimatidis', 'PERSON'), 

In [33]:
Counter([ent for ent in ents if ent[1] == 'GPE']).most_common()

[(('U.S.', 'GPE'), 120),
 (('China', 'GPE'), 60),
 (('Syria', 'GPE'), 49),
 (('New York', 'GPE'), 36),
 (('Japan', 'GPE'), 27),
 (('Mexico', 'GPE'), 21),
 (('Brazil', 'GPE'), 21),
 (('Manhattan', 'GPE'), 16),
 (('New York City', 'GPE'), 15),
 (('Calif.', 'GPE'), 13),
 (('America', 'GPE'), 12),
 (('California', 'GPE'), 11),
 (('Tokyo', 'GPE'), 11),
 (('Washington', 'GPE'), 11),
 (('Australia', 'GPE'), 11),
 (('India', 'GPE'), 9),
 (("New York's", 'GPE'), 9),
 (('Montreal', 'GPE'), 9),
 (('Brooklyn', 'GPE'), 8),
 (('Florida', 'GPE'), 8),
 (('Russia', 'GPE'), 7),
 (('Los Angeles', 'GPE'), 7),
 (('Boston', 'GPE'), 7),
 (('Dallas', 'GPE'), 7),
 (('Texas', 'GPE'), 7),
 (('Frankfurt', 'GPE'), 7),
 (('Taobao', 'GPE'), 7),
 (('Moscow', 'GPE'), 6),
 (('Afghanistan', 'GPE'), 6),
 (('Baltimore', 'GPE'), 6),
 (('N.J.', 'GPE'), 6),
 (('New Jersey', 'GPE'), 6),
 (('Conn.', 'GPE'), 5),
 (('Miami', 'GPE'), 5),
 (('San Francisco', 'GPE'), 5),
 (('Houston', 'GPE'), 5),
 (('France', 'GPE'), 5),
 (('German

In [34]:
Counter([ent for ent in ents if ent[1] == 'ORG']).most_common()

[(('Congress', 'ORG'), 40),
 (('Fed', 'ORG'), 29),
 (('Instagram', 'ORG'), 21),
 (('House', 'ORG'), 18),
 (('S&P', 'ORG'), 18),
 (('Treasury', 'ORG'), 17),
 (('Senate', 'ORG'), 17),
 (('Social Security', 'ORG'), 17),
 (('Realogy', 'ORG'), 16),
 (('Apollo', 'ORG'), 16),
 (('IOC', 'ORG'), 15),
 (('FCC', 'ORG'), 14),
 (('CFTC', 'ORG'), 13),
 (('Neiman', 'ORG'), 12),
 (('P&G', 'ORG'), 12),
 (('Lehman', 'ORG'), 11),
 (("Moody's", 'ORG'), 11),
 (('Medicare', 'ORG'), 10),
 (('Labor', 'ORG'), 10),
 (('The Wall Street Journal', 'ORG'), 9),
 (('IBM', 'ORG'), 9),
 (("Sotheby's", 'ORG'), 9),
 (('AIG', 'ORG'), 8),
 (('Taliban', 'ORG'), 8),
 (('the White House', 'ORG'), 8),
 (('Giants', 'ORG'), 8),
 (('GOP', 'ORG'), 7),
 (('Saks', 'ORG'), 7),
 (('Peugeot', 'ORG'), 7),
 (('White House', 'ORG'), 6),
 (('TARP', 'ORG'), 6),
 (('Bear Stearns', 'ORG'), 6),
 (('Dodd-Frank', 'ORG'), 6),
 (('Goldman', 'ORG'), 6),
 (('City Council', 'ORG'), 6),
 (('NFL', 'ORG'), 6),
 (('Vivendi', 'ORG'), 6),
 (('the Reserve P

## Parsing HTML

In [35]:
# Setup

FASB_standards_URL = 'http://www.fasb.org/jsp/FASB/Page/SectionPage&cid=1176156316498'

In [36]:
response = requests.get(FASB_standards_URL)

In [37]:
response.status_code

200

In [38]:
response.text

'\n\n\n\n\n\n\n\n\n\n  \n\t\n\t\t\n\t\t \n\t\t \n\t\t\n\t\t\n\t\t\t\n\t\t\t\t\n\t\t\t\t\n\t\t\t\t\n\t\t\t\t\t\n\t\t\t\t\t\n\t\t\t\t\t\n\t\t\t\t\t  \n\t\t\t\t\n\t\t\t\t\n\t\t\t\t\n\t\t\t\t\t\n\t\t\t\t\n\n\t\t\t\t \n\t\t\t\t \n\t\t\t\t\n\t\t\t\t\n\t\t\t\t\n\t\t\t\t\n\t\t\t\t\n\t\t\t\t \n\t\t\t\t\t\n\t\t\t\t\t\t\n\t\t\t\t\t\t \n\t\t\t\t\t\t\n\t\t\t\t\t\t\n\t\t\t\t\t\t \n\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t\t  \n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\n\t\t\t\t\t\t\t\n\t\t\t\t\t\t\n\t\t\t\t\t\n\t\t\t\t\t\n\t\t\t\t\n\t\t\t\n\t\t\t\n\t\t\n\t\n\t\n\n\n\n\t\n\t  \n\t    \n<!DOCTYPE html>\n<!--[if lt IE 7]>      <html class="no-js lt-ie9 lt-ie8 lt-ie7"> <![endif]-->\n<!--[if IE 7]>         <html class="no-js lt-ie9 lt-ie8"> <![endif

In [39]:
soup = BeautifulSoup(response.text, 'html.parser')

In [40]:
print(soup.prettify())

<!DOCTYPE html>
<!--[if lt IE 7]>      <html class="no-js lt-ie9 lt-ie8 lt-ie7"> <![endif]-->
<!--[if IE 7]>         <html class="no-js lt-ie9 lt-ie8"> <![endif]-->
<!--[if IE 8]>         <html class="no-js lt-ie9"> <![endif]-->
<!--[if gt IE 8]><!-->
<html class="no-js">
 <!--<![endif]-->
 <head>
  <meta charset="utf-8"/>
  <meta content="IE=edge,chrome=1" http-equiv="X-UA-Compatible"/>
  <meta content="" name="description"/>
  <meta content="width=1024" name="viewport"/>
  <title>
   Accounting Standards Updates Issued
  </title>
  <link href="/cs/fasb/css/main.css" rel="stylesheet"/>
  <!-- Load fancy box for featured video popup -->
  <!-- 2.1.4
	<link rel="stylesheet" href="/cs/fasb/js/fancybox/2.1.4/jquery.fancybox.css" type="text/css" media="screen" />
	-->
  <link href="/cs/fasb/js/fancybox/1.3.4/fancybox/jquery.fancybox-1.3.4.css" media="screen" rel="stylesheet" type="text/css"/>
  <!-- Load camera for slideshow galleries -->
  <link href="/cs/fasb/js/camera/1.3.4/css/camera.c

In [41]:
# The headers of each set of standards
soup.find_all('h3')

[<h3><a name="2021"></a>Issued In 2021</h3>,
 <h3><a name="2020"></a>Issued In 2020</h3>,
 <h3><a name="2019"></a>Issued In 2019</h3>,
 <h3><a name="2018"></a>Issued In 2018</h3>,
 <h3><a name="2017"></a>Issued In 2017</h3>,
 <h3><a name="2016"></a>Issued In 2016</h3>,
 <h3><a name="2015"></a>Issued In 2015</h3>,
 <h3><a name="2014"></a>Issued In 2014</h3>,
 <h3><a name="2013"></a>Issued In 2013</h3>,
 <h3><a name="2012"></a>Issued In 2012</h3>,
 <h3><a name="2011"></a>Issued In 2011</h3>,
 <h3><a name="2010"></a>Issued In 2010</h3>,
 <h3><a name="2009"></a>Issued In 2009</h3>]

In [42]:
header1 = soup.find_all('h3')[0]

In [43]:
urls1 = header1.next_sibling
urls1

'\n'

In [44]:
urls1 = header1.next_sibling.next_sibling
urls1

<ul>
<li><a href="/cs/ContentServer?c=Document_C&amp;pagename=FASB%2FDocument_C%2FDocumentPage&amp;cid=1176177037677">Update 2021-06</a>—Presentation of Financial Statements (Topic 205), Financial Services—Depository and Lending (Topic 942), and Financial Services—Investment Companies (Topic 946): Amendments to SEC Paragraphs Pursuant to SEC Final Rule Releases No. 33-10786, <em>Amendments to Financial Disclosures about Acquired and Disposed Businesses, </em>and No. 33-10835, <em>Update of Statistical Disclosures for Bank and Savings and Loan Registrants  </em>(SEC Update)<br/>
	 </li>
<li><a href="/cs/ContentServer?c=Document_C&amp;pagename=FASB%2FDocument_C%2FDocumentPage&amp;cid=1176176938313">Update 2021-05</a>—Leases (Topic 842): Lessors—Certain Leases with Variable Lease Payments<br/>
	 </li>
<li><a href="/cs/ContentServer?c=Document_C&amp;pagename=FASB%2FDocument_C%2FDocumentPage&amp;cid=1176176593141">Update 2021-04</a>—Earnings Per Share (Topic 260), Debt—Modifications and Ext

In [45]:
for url in urls1.find_all('a'):
    print(url.text, url.get('href'))

Update 2021-06 /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176177037677
Update 2021-05 /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176176938313
Update 2021-04 /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176176593141
Update 2021-03 /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176176428664
Update 2021-02 /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176175985397
Update 2021-01 /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176175899139


The above is pretty good, and will parse most files correctly already.  However, there is a second format that FASB likes to use, which is exhibited by Update No. 2014-09.

The below code picks out this entry.

In [46]:
problem = soup.find_all('h3')[7].next_sibling.next_sibling.find_all('li')[9]
problem

<li><a name="ASU2014-09"></a>Update No. 2014-09—Revenue from Contracts with Customers (Topic 606)
	<ul>
<li><a href="/cs/ContentServer?c=Document_C&amp;pagename=FASB%2FDocument_C%2FDocumentPage&amp;cid=1176164076069">Section A</a>—Summary and Amendments That Create Revenue from Contracts with Customers (Topic 606) and Other Assets and Deferred Costs—Contracts with Customers (Subtopic 340-40)</li>
<li><a href="/cs/ContentServer?c=Document_C&amp;pagename=FASB%2FDocument_C%2FDocumentPage&amp;cid=1176164076098">Section B</a>—Conforming Amendments to Other Topics and Subtopics in the Codification and Status Tables</li>
<li><a href="/cs/ContentServer?c=Document_C&amp;pagename=FASB%2FDocument_C%2FDocumentPage&amp;cid=1176164076149">Section C</a>—Background Information and Basis for Conclusions  </li>
</ul>
</li>

As we can see, this update contains a bunch of `<li>` tags each with a URL of their own.  In this case, we would want to parse them all, but tie them back to the same standard.

Also, note that since this format is interspersed with normally formatted entries, we cannot reliably use the approach used for 2021 in other years.  Instead, we should find all list items (`<li>` tags), and check the format before extracting the URL and name.

In [47]:
problem.a.get('name')

'ASU2014-09'

In [48]:
for li in problem.find_all('li'):
    print(li.a.text, li.a.get('href'))

Section A /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176164076069
Section B /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176164076098
Section C /cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176164076149


### Final parser

In [49]:
year_headings = soup.find_all('h3')
head = year_headings[5]
li_items = head.next_sibling.next_sibling.find_all('li')
li_items[19].parent.parent.name

'li'

In [50]:
def parse_FASB_standards():
    # URL to parse
    FASB_standards_URL = 'https://www.fasb.org/jsp/FASB/Page/SectionPage&cid=1176156316498'
    FASB_base_URL = 'https://www.fasb.org'
    
    # Get the page
    response = requests.get(FASB_standards_URL)
    
    # Make sure the connection was accepted (status of 200)
    if response.status_code != 200:
        print('Check your internet connection')
        return [], []
    
    # Parse with bs4
    soup = BeautifulSoup(response.text, 'html.parser')
    
    # Pull every year
    year_headings = soup.find_all('h3')
    
    # Store output here
    header = ['Year', 'Filing', 'URL']
    output = []
    
    # Iterate over each year in the websites
    for head in year_headings:
        # Extract out the year from the header
        year = int(head.text[-4:])
        li_items = head.next_sibling.next_sibling.find_all('li')
        for li in li_items:
            if li.a.get('href') is None:
                # This is a grouped set of URLs
                name = li.a.get('name')
                for subli in li.find_all('li'):
                    output.append([year, name + '-' + subli.a.text, FASB_base_URL + subli.a.get('href')])
            else:
                if li.parent.parent.name == 'li':
                    # This is a sub-item of a grouped set of URLs -- already parsed
                    pass
                else:
                    # This is a standard URL
                    output.append([year, li.a.text, FASB_base_URL + li.a.get('href')])
    return header, output

header, FASB_standards = parse_FASB_standards()

At this point, you would expect to be able to toss the list of URLs to your favorite downloader (such as `wget`) and grab them all.  Unfortunately, that is not the case, as each URL above goes to a disclaimer page asking you to accept the TOS.

This is easy to get around: after you accept, FASB's webpage just adds `&acceptedDisclaimer=true` to the end of the URL.  We can add this ourselves with a list comprehension.

In [51]:
disclaimer_workaround = '&acceptedDisclaimer=true'
FASB_standards = [[year, name, url + disclaimer_workaround] for year, name, url in FASB_standards]

In [52]:
FASB_standards[0]

[2021,
 'Update 2021-06',
 'https://www.fasb.org/cs/ContentServer?c=Document_C&pagename=FASB%2FDocument_C%2FDocumentPage&cid=1176177037677&acceptedDisclaimer=true']

In [54]:
with open('../../Data/FASB_standard_urls.csv', 'wt', newline='') as f:
    writer = csv.writer(f)
    writer.writerow(header)
    writer.writerows(FASB_standards)

#### Grabbing the files

There is a second issue with downloading the FASB files which we will now have to address.  When you go to the links we found in your browser, you will find yourself on a PDF document as expected.  However, this isn't actually a PDF document!  it is a PDF document embedded in an iframe on a webpage.  As such, when downloading we need to scrape the *actual* URL to the PDF first!

The below code solves this issue by using two calls to requests.  The first call gets the page with the iframe and determines 

In [ ]:
if not os.path.exists('../../Data/FASB_PDFs'):
    os.mkdir('../../Data/FASB_PDFs')

for doc in FASB_standards:
    if not os.path.exists('../../Data/FASB_PDFs/' + doc[1] + '.pdf'):
        response1 = requests.get(doc[2])
        soup = BeautifulSoup(response1.text, 'html.parser')
        pdf_url = 'https://www.fasb.org' + soup.find_all("iframe", {"id": "document"})[0].get('src')
        response2 = requests.get(pdf_url)
        with open('../../Data/FASB_PDFs/' + doc[1] + '.pdf', 'wb') as f:
            f.write(response2.content)

### What if you want to parse out the PDFs now?

There are a lot of libraries to do this in python, such as `pdfminer`, `PyPDF2`, `tika`, `pdfplumber`, etc.

My preferred tools are `pdfminer` and `textract`.  The [pdfminer](https://pdfminersix.readthedocs.io/en/latest/) package is quite powerful for working with PDF files, and has fairly good text extractions.  The [textract](https://textract.readthedocs.io/en/stable/) package is also good at this, but is more broad-based, supporting Microsoft Word and PowerPoint files as well, along with being able to OCR images and do speech-to-text for audio.  You can actually plug `pdfminer.six` into `textract` to make use of both as well.